## Geocoding and Isolines Services

This example illustrates how to combine both the Geocoding and Isolines Data Services.

_Note: You'll need [CARTO Account](https://carto.com/signup) credentials to reproduce this example._

In [1]:
from cartoframes.auth import set_default_credentials

set_default_credentials('creds.json')

In [2]:
from pandas import DataFrame

df = DataFrame([
         ['Calle Serrano 15'],
         ['Calle de San Pedro 21'],
         ['Calle Gran Vía 46'],
         ['Paseo de la Castellana 200'],
         ['Calle Ntra. Sra. del Carmen 7'],
         ['Calle de San Germán 12'],
         ['Calle de Bravo Murillo 377'],
    ],
    columns=['address']
)
df

address
0               Calle Serrano 15
1          Calle de San Pedro 21
2              Calle Gran Vía 46
3     Paseo de la Castellana 200
4  Calle Ntra. Sra. del Carmen 7
5         Calle de San Germán 12
6     Calle de Bravo Murillo 377

In [3]:
from cartoframes.data.services import Geocoding

gc = Geocoding()
gdf, metadata = gc.geocode(df, street='address', city={'value': 'Madrid'}, country={'value': 'Spain'})

Success! Data geocoded correctly


In [4]:
gdf

the_geom                        address  gc_status_rel  \
0  POINT (-3.68831 40.42478)               Calle Serrano 15           0.82   
1  POINT (-3.69488 40.41089)          Calle de San Pedro 21           0.95   
2  POINT (-3.70588 40.42049)              Calle Gran Vía 46           0.92   
3  POINT (-3.68898 40.46239)     Paseo de la Castellana 200           0.95   
4  POINT (-3.70221 40.45840)  Calle Ntra. Sra. del Carmen 7           0.98   
5  POINT (-3.69286 40.45651)         Calle de San Germán 12           0.95   
6  POINT (-3.69093 40.46575)     Calle de Bravo Murillo 377           0.95   

                 carto_geocode_hash  
0  26a9e50f26e86d071fa0ff46b9291863  
1  905794cd20618c2d43d7e4c8db56436c  
2  8bcb00020040f7a01edb6085c7833d2a  
3  35861fd39af822c3fa5c7b562625cdcc  
4  7abee54b2d67041fe1ad4f8f5f19a981  
5  3db89bbedd49ce477cc3f35f4f4a3aae  
6  b1e0a4698eb9a56278614aeb35106bf6

In [5]:
metadata

{'total_rows': 7,
 'required_quota': 7,
 'previously_geocoded': 0,
 'previously_failed': 0,
 'records_with_geometry': 0,
 'final_records_with_geometry': 7,
 'geocoded_increment': 7,
 'successfully_geocoded': 7,
 'failed_geocodings': 0}

In [6]:
from cartoframes.viz import Layer

Layer(gdf)

In [7]:
from cartoframes.data.services import Isolines

iso_service = Isolines()
isochrones = iso_service.isochrones(gdf, [100, 200, 300], mode='walk', dry_run=True)

print('Available Quota: {0}'.format(iso_service.available_quota()))
print('Required Quota: {0}'.format(isochrones.metadata.get('required_quota')))

Available Quota: 115480
Required Quota: 21


In [8]:
isochrones = iso_service.isochrones(gdf, [100, 200, 300], mode='walk')

isochrones.data.head()

Success! Isolines created correctly


source_id  data_range                                           the_geom
0          0         100  MULTIPOLYGON (((-3.68926 40.42557, -3.68797 40...
1          0         200  MULTIPOLYGON (((-3.69012 40.42574, -3.68986 40...
2          0         300  MULTIPOLYGON (((-3.69081 40.42643, -3.69055 40...
3          1         100  MULTIPOLYGON (((-3.69544 40.41183, -3.69484 40...
4          1         200  MULTIPOLYGON (((-3.69630 40.41132, -3.69621 40...

In [9]:
from cartoframes.viz import Map, Layer, basic_style

Map([
    Layer(isochrones.data, basic_style(color='green', opacity='0.3')),
    Layer(gdf, basic_style(size=3))
])